In [1]:
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
import tifffile as tf
from scipy.ndimage.filters import gaussian_filter1d as gaussian
from glob import glob
from scipy.signal import savgol_filter, medfilt
from math import floor
import matplotlib.ticker as ticker
from scipy.optimize import curve_fit

In [2]:
# 1. load data into pandas data frame

# 2. convert data from I(t) to c_i(t) via equation for G quadruplex binding
    # - find t0
    # - 
# 3. calculate dc_i/dt for each GUV

# 4. calculate background intensity and convert this to c_0(t) via g quadruplex binding model

# 5. plot dc_/dt/A_GUV vs c_0-c_i (expect to see a positive linear relationship)


# as data includes actual G4 background for GUV permeability and later Gramicidin A experiments, start with these experiments


In [3]:
App = 3.16 #um^2
Amin= 40*App*1e-12 #m^2
# G quadruplex model binding


def exp_I(c, k = 8.8,A = 0.39):
    return  A+ (1-A)/(k_1*c**2+1)

def inv(I, k = 8.8,A = 0.39):
    
    if I > 1:
        return 0
    
    elif I < A:
        return 1
        
    else:
        return np.sqrt((1/k)*((1-A)/(I-A)-1))


#smoothing configs

sigma = 101




# Calibration model fit


**If you have already fitted a calibration function and saved the parameters skip this section**


In [4]:
fitsdf = pd.read_csv('../Calibrations/Calibration_approx_fit_params.csv')

fit = fitsdf['Fitting Params']

def fit_func(I,fit):
    
    c = np.zeros_like(I)
    
    for i in range(1,len(fit)+1):

        c += fit[i-1]*(-np.log(I))**(len(fit)-i)
        print(len(fit)-i)
    return c

In [5]:

t0 = 50
t1 = 150
dt = 30/60

In [6]:
# load 260pM Gramicidin A experiment

dfI = pd.read_csv('../KineticsofLeakageGUV/collatedIabs.csv')
dfA = pd.read_csv('../KineticsofLeakageGUV/collatedAabs.csv')

In [7]:
dfI = dfI.iloc[:,1:]
dfA = dfA.iloc[:,1:]

In [8]:
dfA = dfA.fillna(0)
dfI = dfI.fillna(0)

# Remove small detected objects, most likely not GUVs

**check that the size is appropriate for the experiment**

In [9]:
# Remove small detected objects, most likely not GUVs
App = 3.16 #um^2
Amin= 75*App*1e-12 #m^2


for col in dfI.columns:
    
    if col in dfA.columns:
        area = 1e-12*App*np.mean(dfA[col].iloc[:30])
        
        if area < Amin:
            dfI.pop(col)
            dfA.pop(col)

# Remove intensity curves with sudden drops
 These are likely from GUVs suddenly escaping the trap

In [10]:

def remove_burst_events(data,threshold = 0.45):
    
    for column in data.columns:
        
        if len(data[column][data[column] < threshold]) >=1:
            data.pop(column)
            

In [11]:
# normalise intensities

for col in dfI.columns:
    dfI[col] = dfI[col]/np.mean(dfI[col][:10])
remove_burst_events(dfI)


%matplotlib qt
fig, ax = plt.subplots(1,1)

for col in dfI.columns:
    ax.plot(dfI[col].iloc[t0:])

# Smooth data

## Smoothing strategy

1. In experiments where there was relatively fast decay in intensity initially, but slows down (as exponential decays do..), yet there is still a lot of noise, it may be necessary to smooth different regions with different 'cutoff's.
When the intensity has dropped, the signal to noise drops. What's more during the slower period of intensity decay, there is increasing likelihood that some long timescale event will have happened to distort the data. This long timescale noise may be of a similar timescale to the 'signal' in the early period of rapid decay. 

2. The **solution** chosen here, is to have the user select a timepoint to bisect the time traces. The early period up until that timepoint is smoothed with the 1st user input smoothing parameter (usually between 11-21). Then the later period of slow decay is smoother with much larger smoothing settings (50-80). In order to ensure a smooth 'stitching' of these differently smoothed traces, we concatenate and repeat the smoothing with the smallest of the two specified smoothing parameters.

In [12]:
def smooth_decay(I,t0,t1=-1,smoothing_0 = 19,smoothing_1 = 81):
    
    
    if smoothing_0 > t1-t0 and t1 != -1:
        raise ValueError('Smoothing parameter cannot be greater than input data')
    
    smoothed_decay_0 = I.iloc[t0:t1]
    
    smoothed_decay_0 = savgol_filter(smoothed_decay_0,smoothing_0,1)
    
    if t1 != -1:
        
        smoothed_decay_1 = I.iloc[t1:]
        smoothed_decay_1  = savgol_filter(smoothed_decay_1,smoothing_1,1)
        
        smoothed_decay = np.concatenate((smoothed_decay_0,smoothed_decay_1))
    else:
        smoothed_decay = smoothed_decay_0
                               
    final_smoothed_decay = savgol_filter(smoothed_decay,smoothing_0,1)
    return final_smoothed_decay
                                  
                            

In [13]:
#Check smoothing still fits data
#
num = 8
fig,axs = plt.subplots(1,num)

for i,col in enumerate(dfI.columns[np.random.randint(0,len(dfI.columns),num)]):
    
    axs[i].plot(dfI[col].iloc[t0:])
    axs[i].plot(smooth_decay(dfI[col],t0,t1,smoothing_0 = 91,smoothing_1=151))
    

In [14]:
dfC_dict = {}

# can't exploit numpy broadcasting

for col in dfI.columns:
    
    smoothed_decay = smooth_decay(dfI[col],t0,t1,smoothing_0 = 51,smoothing_1=81)
#     print(smoothed_decay)
#     normalised_sd = smoothed_decay/np.mean(smoothed_decay[:30])
    
    cs = []
    for I in smoothed_decay:
#         print(I)
        cs.append(fit_func(I,fit))
    
    
    dfC_dict[col] = cs
    
dfC = pd.DataFrame(dfC_dict)

3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1


0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1


1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2


...

2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3


3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1


1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2


3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


In [15]:
%matplotlib qt

fig, axs = plt.subplots(1,2)

t = dt*np.arange(0,len(dfC))
for col in dfC.columns:
    
    
    axs[0].plot(t,dfC[col])
    axs[1].plot(t,dfI[col].iloc[t0:])
    

    for ax in axs:
        ax.set_ylim([0,1])



In [16]:
# find representative background concentration variation

# tifs = glob('/media/marcus/9C33-6BBD/20210920_GramA_260pM07_3nM815_1mMKCl_1/260pM/*.tif')

# bgs = []

# fig, ax = plt.subplots(1,1)

# for tif in tifs:
    
#     vid = tf.TiffFile(tif)
    
#     frames = vid.asarray()
    
#     bg = np.median(frames,axis  =(1,2))
#     bg = np.array(bg)/np.max(bg)
#     bgs.append(bg)
    
    
#     ax.plot(bg)

# This confirms that the normalised background is the same for each chamber. Suggesting potassium concs are identical between chambers



In [21]:
# filter concentration data by gradient
# if 

fig, axs = plt.subplots(1,2)

for col in dfC.columns:
    
#     grad = np.gradient(gaussian(dfC[col],sigma = 5))
    
#     if len(grad[grad <= -0.0009])/len(grad) > 0.05:
#         dfC.pop(col)
#         continue
#     axs[0].hist(grad,15)
#     axs[1].plot(dfC[col])

NameError: name 'grad' is not defined

In [33]:
tifs = glob('/media/marcus/9C33-6BBD/20210427_OmpF_PCPG_KCL_Flush_2-20210427T184510Z-002/20210427_OmpF_PCPG_KCL_Flush_2/*.tif')
tif = tifs[-1]

vid = tf.TiffFile(tif)

frames = vid.asarray()
bg = np.median(frames,axis = (1,2))

bg = np.array(bg)-np.mean(bg[:30])
bg = bg/np.max(bg)



OME series: not an ome-tiff master file


In [73]:
bg

array([ 0.0416429 ,  0.06446092,  0.00741586, -0.02681118, -0.01540217,
       -0.00969766, -0.02110667, -0.01540217, -0.03251569,  0.00171135,
       -0.00969766,  0.00741586,  0.00171135, -0.01540217, -0.02681118,
       -0.02110667, -0.00399315,  0.01882487,  0.00171135,  0.00171135,
        0.01882487,  0.01312037, -0.00399315,  0.01312037,  0.03023388,
        0.01312037,  0.00171135, -0.01540217, -0.00399315, -0.01540217,
        0.00171135, -0.00399315, -0.02110667, -0.00969766,  0.00171135,
        0.00171135, -0.00399315, -0.00399315, -0.01540217, -0.01540217,
        0.00741586,  0.01312037,  0.00741586,  0.01312037,  0.01312037,
       -0.00969766, -0.00969766, -0.02110667,  0.00741586,  0.01312037,
       -0.03251569, -0.00399315, -0.00399315, -0.00969766, -0.01540217,
       -0.00969766, -0.00969766, -0.02110667,  0.03023388,  0.00741586,
        0.0416429 ,  0.00171135, -0.00399315,  0.01882487,  0.02452938,
        0.02452938,  0.03593839,  0.00741586,  0.00741586,  0.04

In [131]:
# c_bg = []
# for x in bg[360+t0:]:
#     c_bg.append(inv(x))

In [132]:
# fig, axs = plt.subplots(1,2)


# smoothed_background = gaussian(c_bg,sigma)
# axs[0].plot(smoothed_background)
# axs[1].plot(bg[360+t0:])

In [80]:
# drift in the background intensity over time, once the potassium has arrived, is causing a drifting predicted potassium concentration
# this is unlikely to be the case in reality.
# Therefore the best thing may be to just assume that after an initial 80 frame boundary region (20 mins) for this exp
# the potassium concentration externally reaches 1mM.


# Find concentration difference

In [17]:
# calculating c_ext - c_i

dfdeltaC_dict = {}

for col in dfC:
    
    dfdeltaC_dict[col] = 1-dfC[col]
    
dfdeltaC = pd.DataFrame(dfdeltaC_dict)

In [18]:
fig, axC = plt.subplots(1,1)

delete_cols = []

for col in dfdeltaC.columns:
    graddeltaC = np.gradient(dfdeltaC[col])
    
    
    if len(graddeltaC[graddeltaC > 0]) > 1:
        delete_cols.append(col)
        continue
        
    axC.plot(dfdeltaC[col])

In [19]:
for col in delete_cols:
    dfdeltaC.pop(col)

# Determine the flux

In [20]:
# now calculate J

# J = (1/A)*dN/dt = R/3* dc_i/dt

dfJ_dict = {}


for col in dfdeltaC:
    
    if col in dfA:
        print(col)
        delta_c = np.gradient(dfC[col],dt)/60 #molm^-3s^-1
        print(dfC[col])
        A = np.mean(dfA[col].iloc[:30])*App*1e-12 #m^2
#         if A < Amin:
#             continue
        R = np.sqrt(A/np.pi) #m
        
        dfJ_dict[col] = R/3*delta_c #molm^-2s^-1
        

dfJ = pd.DataFrame(dfJ_dict)



10070
0      0.058778803605750246
1       0.06069924340924812
2       0.06261343634209604
3       0.06452139385067514
4       0.06642312756353767
5       0.06831864929312244
6       0.07020797103748855
7        0.0720911049820644
8       0.07396806350141473
9        0.0758388591610227
10      0.07770350471909099
11      0.07956201312835895
12      0.08141439753793835
13      0.08326067129516515
14      0.08510084794747066
15      0.08693494124427004
16       0.0887629651388688
17      0.09058493379038883
18      0.09240086156571115
19      0.09421076304143916
20      0.09601465300588005
21      0.09781254646104612
22      0.09960445862467415
23       0.1013904049322658
24      0.10317040103914704
25      0.10494446282254885
26       0.1067031594101722
27      0.10841144887375127
28      0.11007757749059198
29      0.11170394501298245
               ...         
720      0.4847747236385672
721      0.4852606306719905
722       0.485744151623118
723       0.486236120286062
724     0.4867

In [24]:
fig, axs = plt.subplots(1,3)
legend = []

for col in dfJ.columns:

    legend.append(col)
#     print(dfdeltaC)

    axs[0].scatter(dfdeltaC[col],dfJ[col]*1e10, marker = '+', s = 10)
    print(dfJ[col])

    axs[1].plot(dt*np.arange(0,len(dfC[col])),dfC[col])

    
#     gradients = []
#     win = 10
#     for i in range(dfJ[col].shape[0]-(win-1)):
        
#         gradient = np.mean(np.gradient(dfJ[col].iloc[i:i+win]))
#         gradients.append(gradient)
        
    
    axs[2].plot(np.gradient(dfJ[col],dfdeltaC[col]))
axs[0].tick_params(direction = 'in',left = True,right = True,bottom = True,top = True,length = 6)
axs[1].tick_params(direction = 'in',left = True,right = True,bottom = True,top = True,length = 6)
axs[0].set_xlabel('[K_ext]-[K_int] [mM]',fontsize = 18)

axs[0].set_ylabel('J [molm^-2s^-1]',fontsize = 18)

axs[1].set_ylabel('[K_int] [mM]',fontsize = 18)


axs[1].set_xlabel(' T [mins]',fontsize = 18)


#xticks

axs[0].set_xticks([0,0.5,1])
axs[0].set_xticklabels([0,0.5,1],fontsize = 15)
axs[0].set_xlim([0,1.05])

axs[1].set_xticks([0,60,120])
axs[1].set_xticklabels([0,60,120],fontsize = 15)

#yticks

axs[0].set_yticks([0,0.01,0.02])
axs[0].set_yticklabels([0,0.01,0.02],fontsize = 15)

axs[0].set_ylim([-0.0005,0.0105])
axs[1].set_yticks([0, 0.5,1])
axs[1].set_yticklabels([0,0.5,1],fontsize = 15)


axs[0].set_ylim([-0.0005,0.0205])
axs[1].set_ylim([-0.05,1.05])


plt.legend(legend)
#xticks

# axs[0].set_xticks([0.5,0.75,1])
# axs[0].set_xticklabels([0.5,0.75,1],fontsize = 15)

# axs[1].set_xticks([0,20,40])
# axs[1].set_xticklabels([0,20,40],fontsize = 15)

# #yticks

# axs[0].set_yticks([0,0.005,0.01,0.015])
# axs[0].set_yticklabels([0,0.005,0.01,0.015],fontsize = 15)

# axs[0].set_ylim([-0.0005,0.0155])
# axs[1].set_yticks([0, 0.25,0.5])
# axs[1].set_yticklabels([0,0.25,0.5],fontsize = 15)


# plt.rcParams['text.usetex'] = True

# def myticks(x,pos):

#     if x == 0: return "$0$"

#     exponent = int(np.log10(x))
#     coeff = x/10**exponent

#     return r"${:2.0f} \times 10^{{ {:2d} }}$".format(coeff,exponent)

# axs[0].yaxis.set_major_formatter(ticker.FuncFormatter(myticks))

0     -1.102303e-10
1     -1.103175e-10
2     -1.104919e-10
3     -1.106664e-10
4     -1.108410e-10
5     -1.110156e-10
6     -1.111903e-10
7     -1.113652e-10
8     -1.115401e-10
9     -1.117151e-10
10    -1.118901e-10
11    -1.120653e-10
12    -1.122405e-10
13    -1.124158e-10
14    -1.125912e-10
15    -7.096613e-11
16     3.515280e-11
17     6.471061e-11
18     4.345679e-11
19     1.577636e-11
20     3.409599e-11
21     1.601379e-10
22     2.891808e-10
23     3.131903e-10
24     3.406772e-10
25     3.763054e-10
26     3.528160e-10
27     3.699455e-10
28     4.398507e-10
29     5.559377e-10
           ...     
720    4.536191e-11
721    3.745601e-11
722    3.875644e-11
723    3.947755e-11
724    4.938580e-11
725    5.902375e-11
726    5.903690e-11
727    5.905095e-11
728    5.906593e-11
729    5.908183e-11
730    5.909866e-11
731    5.911643e-11
732    5.913513e-11
733    5.915478e-11
734    5.917538e-11
735    5.919693e-11
736    5.921943e-11
737    5.924290e-11
738    5.926733e-11


0     -2.064149e-10
1     -2.066500e-10
2     -2.071203e-10
3     -2.075909e-10
4     -2.080617e-10
5     -2.085327e-10
6     -2.090040e-10
7     -2.094754e-10
8     -2.099471e-10
9     -2.104191e-10
10    -2.108912e-10
11    -2.113635e-10
12    -2.118361e-10
13    -2.123088e-10
14    -2.127817e-10
15    -2.467327e-10
16    -2.933749e-10
17    -3.152250e-10
18    -3.085888e-10
19    -2.797796e-10
20    -2.773985e-10
21    -2.848464e-10
22    -2.901848e-10
23    -2.954781e-10
24    -3.382442e-10
25    -3.809824e-10
26    -4.271844e-10
27    -4.898611e-10
28    -4.996856e-10
29    -4.831507e-10
           ...     
720    8.565342e-11
721    8.349514e-11
722    8.451765e-11
723    8.627107e-11
724    8.398350e-11
725    8.333823e-11
726    8.322650e-11
727    8.311493e-11
728    8.300350e-11
729    8.289223e-11
730    8.278111e-11
731    8.267014e-11
732    8.255932e-11
733    8.244865e-11
734    8.233814e-11
735    8.222779e-11
736    8.211759e-11
737    8.200755e-11
738    8.189766e-11


0      3.328151e-11
1      3.327539e-11
2      3.326314e-11
3      3.325089e-11
4      3.323865e-11
5      3.322640e-11
6      3.321416e-11
7      3.320192e-11
8      3.318967e-11
9      3.317743e-11
10     3.316519e-11
11     3.315296e-11
12     3.314072e-11
13     3.312848e-11
14     3.311625e-11
15     3.056931e-11
16     2.903912e-11
17     2.972113e-11
18     2.936524e-11
19     3.129696e-11
20     3.141796e-11
21     3.260100e-11
22     3.441505e-11
23     3.255359e-11
24     3.204246e-11
25     3.415993e-11
26     3.809257e-11
27     3.981778e-11
28     4.123104e-11
29     4.180838e-11
           ...     
720    1.528421e-11
721    1.417534e-11
722    1.275749e-11
723    1.191801e-11
724    1.222366e-11
725    1.264113e-11
726    1.263864e-11
727    1.263615e-11
728    1.263366e-11
729    1.263117e-11
730    1.262868e-11
731    1.262619e-11
732    1.262371e-11
733    1.262122e-11
734    1.261873e-11
735    1.261624e-11
736    1.261376e-11
737    1.261127e-11
738    1.260879e-11


0     -3.112126e-11
1     -3.112662e-11
2     -3.113735e-11
3     -3.114808e-11
4     -3.115882e-11
5     -3.116955e-11
6     -3.118028e-11
7     -3.119102e-11
8     -3.120175e-11
9     -3.121249e-11
10    -3.122322e-11
11    -3.123396e-11
12    -3.124470e-11
13    -3.125543e-11
14    -3.126617e-11
15    -1.724775e-11
16    -1.768852e-12
17     6.193491e-12
18     1.269969e-11
19     1.162926e-11
20     1.223277e-11
21     4.294743e-12
22    -5.400765e-12
23    -7.513741e-12
24    -5.264575e-12
25    -7.483070e-12
26    -1.500426e-11
27    -1.949374e-11
28    -1.914515e-11
29    -1.255272e-11
           ...     
720    7.532446e-11
721    7.590476e-11
722    7.642563e-11
723    7.764838e-11
724    7.612049e-11
725    7.496283e-11
726    7.486217e-11
727    7.476170e-11
728    7.466141e-11
729    7.456131e-11
730    7.446139e-11
731    7.436167e-11
732    7.426213e-11
733    7.416278e-11
734    7.406362e-11
735    7.396465e-11
736    7.386587e-11
737    7.376729e-11
738    7.366890e-11


0     -8.059906e-11
1     -8.063741e-11
2     -8.071411e-11
3     -8.079083e-11
4     -8.086757e-11
5     -8.094434e-11
6     -8.102112e-11
7     -8.109791e-11
8     -8.117473e-11
9     -8.125157e-11
10    -8.132842e-11
11    -8.140529e-11
12    -8.148218e-11
13    -8.155909e-11
14    -8.163602e-11
15    -8.123974e-11
16    -7.519054e-11
17    -7.405809e-11
18    -7.753176e-11
19    -7.782768e-11
20    -7.601010e-11
21    -7.705074e-11
22    -7.962215e-11
23    -8.131763e-11
24    -8.605422e-11
25    -8.752332e-11
26    -8.291055e-11
27    -7.575165e-11
28    -7.223584e-11
29    -6.466421e-11
           ...     
720    5.298015e-11
721    5.256956e-11
722    5.321956e-11
723    5.266324e-11
724    5.068630e-11
725    5.063204e-11
726    5.058661e-11
727    5.054124e-11
728    5.049593e-11
729    5.045068e-11
730    5.040548e-11
731    5.036035e-11
732    5.031528e-11
733    5.027026e-11
734    5.022531e-11
735    5.018042e-11
736    5.013558e-11
737    5.009081e-11
738    5.004610e-11


0      1.010132e-10
1      1.009692e-10
2      1.008811e-10
3      1.007931e-10
4      1.007052e-10
5      1.006172e-10
6      1.005293e-10
7      1.004414e-10
8      1.003535e-10
9      1.002657e-10
10     1.001779e-10
11     1.000901e-10
12     1.000023e-10
13     9.991457e-11
14     9.982685e-11
15     1.023794e-10
16     1.040862e-10
17     1.039519e-10
18     1.029883e-10
19     1.001591e-10
20     9.678413e-11
21     9.151868e-11
22     9.535095e-11
23     1.047608e-10
24     1.059615e-10
25     1.043598e-10
26     1.049640e-10
27     1.057774e-10
28     1.058968e-10
29     1.041392e-10
           ...     
720    3.062810e-11
721    3.135791e-11
722    3.255888e-11
723    3.349923e-11
724    3.408394e-11
725    3.436161e-11
726    3.434669e-11
727    3.433177e-11
728    3.431688e-11
729    3.430199e-11
730    3.428712e-11
731    3.427227e-11
732    3.425743e-11
733    3.424261e-11
734    3.422780e-11
735    3.421300e-11
736    3.419822e-11
737    3.418345e-11
738    3.416870e-11


0      3.449485e-11
1      3.448633e-11
2      3.446929e-11
3      3.445226e-11
4      3.443523e-11
5      3.441821e-11
6      3.440118e-11
7      3.438417e-11
8      3.436715e-11
9      3.435014e-11
10     3.433313e-11
11     3.431613e-11
12     3.429913e-11
13     3.428213e-11
14     3.426514e-11
15     5.359867e-11
16     7.382556e-11
17     7.907945e-11
18     7.707996e-11
19     7.222569e-11
20     7.649206e-11
21     8.025201e-11
22     9.680867e-11
23     9.826834e-11
24     8.495078e-11
25     7.646467e-11
26     6.275217e-11
27     6.148067e-11
28     5.873812e-11
29     6.322440e-11
           ...     
720    4.153137e-11
721    4.062273e-11
722    4.008181e-11
723    3.980257e-11
724    3.869864e-11
725    3.777631e-11
726    3.774938e-11
727    3.772251e-11
728    3.769570e-11
729    3.766895e-11
730    3.764226e-11
731    3.761563e-11
732    3.758905e-11
733    3.756254e-11
734    3.753609e-11
735    3.750970e-11
736    3.748336e-11
737    3.745709e-11
738    3.743088e-11


0      3.295256e-11
1      3.294709e-11
2      3.293615e-11
3      3.292522e-11
4      3.291428e-11
5      3.290335e-11
6      3.289242e-11
7      3.288149e-11
8      3.287057e-11
9      3.285964e-11
10     3.284872e-11
11     3.283780e-11
12     3.282688e-11
13     3.281596e-11
14     3.280504e-11
15     4.136597e-11
16     5.737428e-11
17     6.392151e-11
18     5.975069e-11
19     6.684084e-11
20     7.367806e-11
21     7.757517e-11
22     8.935643e-11
23     8.916936e-11
24     8.545295e-11
25     8.536122e-11
26     8.833402e-11
27     9.331664e-11
28     9.439996e-11
29     9.900357e-11
           ...     
720    4.251061e-11
721    4.318914e-11
722    4.359536e-11
723    4.328811e-11
724    4.307880e-11
725    4.302332e-11
726    4.300714e-11
727    4.299105e-11
728    4.297505e-11
729    4.295912e-11
730    4.294328e-11
731    4.292753e-11
732    4.291186e-11
733    4.289627e-11
734    4.288078e-11
735    4.286536e-11
736    4.285003e-11
737    4.283479e-11
738    4.281963e-11


# Plot the Flux against concentration gradient



In [21]:
%matplotlib qt
figJ, axJ = plt.subplots(1,1)
figC, axC = plt.subplots(1,1)


P_threshold = 3.5e-10

def Jfit(deltac,k,c):
    return k*deltac + c

p0 = [1e-14,0]
Pparams = {}
cols = []
for i,col in enumerate(dfJ.columns):
    
    
    t = dt*np.arange(0,len(dfC[col]))
    
    J = dfJ[col]
    deltaC = dfdeltaC[col]
    
#     deltaC_bar = np.linspace(dfC[col].min(),1)
    
    params = curve_fit(Jfit,deltaC.iloc[deltaC.to_numpy().astype(float)<0.95],J.iloc[deltaC.to_numpy().astype(float)<0.95],p0)
    
    J_bar = Jfit(deltaC,*params[0])
    P = params[0][0]
    dP = np.sqrt(params[1][0][0])
    print(dP/P, P)
    
    Pparams[col] = params
    if P < 0:
        continue
        
    if dP/P > 0.1 or P < 0:
        
        continue
        
#     if len(J.iloc[(deltaC < 0.7).to_numpy()]) < 1:
#         continue
    
    cols.append(col)
    
    print(col)
    # plot fluxes
    axJ.scatter(deltaC,J,alpha = 0.25)
    axJ.plot(deltaC,J_bar)
    
    #plot the Intensity vs time
    
    axC.plot(t,dfI[col].iloc[t0:])
 
#Flux plot params


axJ.set_xticks([0.5,1])
axJ.set_xlim([0.45,1.05])
axJ.set_xticklabels([0.5,1],fontsize = 15)

axJ.set_xlabel('$[K]_{ext} - [K]_{in}$ [mM]',fontsize = 18)
axJ.set_yticks([0,5e-11,1e-10,1.5e-10,2e-10])
axJ.set_yticklabels([0,0.5,1,1.5,2],fontsize = 15)

axJ.set_ylim([-1e-11,2.1e-10])
#  
axJ.set_ylabel('J  [$10^{-10}$ mol$m^{-2}s^{-1}$]',fontsize = 18)
axJ.tick_params(direction = 'in',left = True,right = True, top = True, bottom = True,length = 7)

axC.set_xticks([0,20,40])
axC.set_xticklabels([0,20,40],fontsize = 15)
axC.set_xlabel('Time [mins]',fontsize = 18)

axC.set_yticks([0,0.5,1])
axC.set_yticklabels([0,0.5,1],fontsize = 15)
axC.set_ylabel('Rel I',fontsize = 18 )
axC.set_ylim([-0.05,1.05])
# axC.set_xlim([0,45])

# global params

axC.tick_params(direction = 'in',left = True,right = True, top = True, bottom = True,length = 7)


0.030877634824312182 4.082455260154064e-10
10070
0.5768685028018085 2.4831699171349903e-11
0.04038572754826651 1.5708551120870589e-10
07066
-0.049883462780798235 -3.121372863669962e-10
0.03850035652699288 1.6510047968339894e-10
07106
0.08372276652542637 8.293402911844734e-11
07114
0.042137828267895465 9.904723920055048e-11
07148
0.1219255802557547 6.13553368203019e-11
0.14039966579222526 8.832696652644989e-11
0.1250919468187008 1.168154169067706e-10
0.03642473330706785 1.911418648351052e-10
06065
0.027617142218084555 3.1705571673158513e-10
06132
0.022266397563986393 3.484747050374558e-10
06137
0.14242399849249196 9.759641104573188e-11
0.15677465619517494 8.341919528005824e-11
0.06492418407351583 1.4479188921565283e-10
08064
0.06349881613783136 1.4573343348107902e-10
02056
0.07072829422257686 1.6792434948922147e-10
05045
0.0965693962936622 9.995372924489182e-11
05055
0.04999356613415843 1.2686668581778197e-10
05056
0.03888279452634878 3.662309350794502e-10
05104
0.031039897684288983 5.5

# Save Permeability values

In [23]:
P_df = {'P ms^-1': [Pparams[key][0][0] for key in Pparams.keys()],
       'dP/P': [np.sqrt(Pparams[key][1][0][0])/Pparams[key][0][0] for key in Pparams.keys()],
       'A':[np.mean(dfA[key].iloc[:30]) for key in Pparams.keys()]}
        
P_identified = {key:[Pparams[key][0][0]] for key in Pparams.keys()}
P_identified = pd.DataFrame(P_identified)
P_df = pd.DataFrame(P_df)

In [81]:
P_df['P cms^-1'] = P_df['P ms^-1']*100

In [78]:
P_df

P ms^-1      dP/P           A      P cms^-1
0 -3.121373e-10 -0.049883   79.200000 -3.121373e-08
1  1.570663e-10  0.098426  164.666667  1.570663e-08
2  3.484747e-10  0.022266  126.566667  3.484747e-08
3  1.651005e-10  0.038500  100.466667  1.651005e-08
4  3.662309e-10  0.038883  106.533333  3.662309e-08

In [82]:
P_df.to_csv('Permeabilities_GUV.csv')

In [70]:
# model membrane voltage using membrane capacitance

# Q = VC

# V = ze(cK - cCl)*Vol/C

# for a completely potassium selective membrane
# c = 1e-6 #F/cm^-2
c = 1e-2 #F/m^2

C = c*4*np.pi*(1.25e-5)**2

V = (96485*(1)*(4/3)*np.pi*(1.25e-5)**3)/C


# Save Flux vs deltaC data


In [24]:
dfJ.to_csv('Flux_GUV.csv')
dfdeltaC.to_csv('deltaC_GUV.csv')
P_identified.to_csv('PbyGUVId_GUV.csv')

# Compute average J vs deltaC to see if on average there is a membrane potential effect

In [146]:
mins = dfdeltaC.min()

mindeltaC = np.min(mins)
bin_bottom = floor(100*mindeltaC)/100

In [147]:
deltaC_bins = np.linspace(bin_bottom,0.9,100)

In [148]:
deltaC_bins

array([0.45      , 0.45454545, 0.45909091, 0.46363636, 0.46818182,
       0.47272727, 0.47727273, 0.48181818, 0.48636364, 0.49090909,
       0.49545455, 0.5       , 0.50454545, 0.50909091, 0.51363636,
       0.51818182, 0.52272727, 0.52727273, 0.53181818, 0.53636364,
       0.54090909, 0.54545455, 0.55      , 0.55454545, 0.55909091,
       0.56363636, 0.56818182, 0.57272727, 0.57727273, 0.58181818,
       0.58636364, 0.59090909, 0.59545455, 0.6       , 0.60454545,
       0.60909091, 0.61363636, 0.61818182, 0.62272727, 0.62727273,
       0.63181818, 0.63636364, 0.64090909, 0.64545455, 0.65      ,
       0.65454545, 0.65909091, 0.66363636, 0.66818182, 0.67272727,
       0.67727273, 0.68181818, 0.68636364, 0.69090909, 0.69545455,
       0.7       , 0.70454545, 0.70909091, 0.71363636, 0.71818182,
       0.72272727, 0.72727273, 0.73181818, 0.73636364, 0.74090909,
       0.74545455, 0.75      , 0.75454545, 0.75909091, 0.76363636,
       0.76818182, 0.77272727, 0.77727273, 0.78181818, 0.78636

In [137]:
j_np = dfJ.to_numpy()
deltaC_np = dfdeltaC.to_numpy()

In [149]:

j_bar = []
for i in range(len(deltaC_bins[:-1])):
    
    bin_top = deltaC_bins[i+1]
    bin_bottom_tmp = deltaC_bins[i]
    
    j = j_np[deltaC_np < bin_top][deltaC_np[deltaC_np < bin_top] > bin_bottom_tmp]
    
    print(len(j))
    j_bar.append(np.median(j))
    
    
print(j_bar)

0
1
0
1
0
0
0
0
1
2
0
1
1
2
2
0
0
1
2
4
8
3
0
47
29
15
31
17
18
42
41
74
54
80
94
49
75
101
102
141
109
120
136
109
135
100
130
126
192
216
192
184
182
213
215
131
152
244
251
350
292
226
408
573
312
402
559
492
439
737
646
677
732
899
1056
1264
1724
1507
2043
1838
2077
2384
2608
2565
2800
3175
3052
3246
3263
3418
3507
3478
3677
3327
3571
3553
3606
3462
3035
[nan, 9.839751435584963e-16, nan, 1.4745989643494991e-15, nan, nan, nan, nan, 2.4534771806161555e-15, 3.9089127363571864e-15, nan, 5.3458293304146265e-15, 6.287373723412426e-15, 7.668784814108946e-15, 9.449110801645437e-15, nan, nan, 1.0731182291683217e-14, 1.1952441855232956e-14, 8.774764400881585e-16, 1.3491081813759465e-14, 3.6761038913492346e-15, nan, 1.951126532992394e-14, 1.3165313173836345e-14, 1.4166675668132463e-14, 1.4911781173958298e-14, 1.657743196800554e-14, 1.448950452893274e-14, 1.4368512206229044e-14, 1.2756520925199484e-14, 1.1898509226577676e-14, 1.2336507959717815e-14, 1.4821416062302825e-14, 1.2961480179127857e-

/home/marcus/anaconda3/envs/trapperenv/lib/python3.7/site-packages/numpy/core/fromnumeric.py:3118: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/marcus/anaconda3/envs/trapperenv/lib/python3.7/site-packages/numpy/core/_methods.py:85: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


In [150]:
deltaC_bar = 0.5*(deltaC_bins[1:] + deltaC_bins[:-1])

fig, ax = plt.subplots(1,1)


ax.scatter(deltaC_bar,np.array(j_bar)*1e15)